# Visualize tracking dataset

Load a sample from `MedicanesTrackDataset` and overlay the cyclone centre on the video tile.

Set `csv_path` and `data_root` to point to your local data.

In [1]:
import os, re
import numpy as np
import pandas as pd
from arguments import prepare_finetuning_args
from dataset.data_manager import BuildTrackingDataset, DataManager
import torch
from torch.utils.data import DataLoader
from dataset.tracking_dataset import MedicanesTrackDataset
from dataset.build_dataset import get_cyclone_center_pixel
from view_test_tiles import display_video_clip
from PIL import Image, ImageDraw


Impossibile caricare la libreria torch dynamo


In [2]:
# Paths to the annotation CSV and tile frames
csv_path = 'output/traintest_csv/train_manos_w_1238.csv'
data_root = 'PATH/TO/tiles'
args = prepare_finetuning_args()


# Percorsi
input_dir = "../fromgcloud"
output_dir = "../airmassRGB/supervised/" 
csv_out = "train_tracking.csv"          # CSV finale con pixel per tracking
manos_file = "medicane_data_input/manos_CL10_pixel.csv"  #
df_tracks = pd.read_csv(manos_file, parse_dates=['time', 'start_time', 'end_time'])

bt = BuildTrackingDataset(type="supervised", args=args)
bt.prepare_data(df_tracks, input_dir, output_dir)
bt.create_tracking_csv(output_dir, csv_out)


sorted_metadata_files num :  11800
1)  ->
Con cicloni: 110
Senza cicloni: 1054

Creazione delle folder per i 1164 video...	Salvati 0 file - Erano già presenti 18624 file - File totali 18624
1164 video per il periodo (effettivo) da 2012-04-10 19:45:00 a 2012-04-14 21:00:00

2)  ->
Con cicloni: 122
Senza cicloni: 1150

Creazione delle folder per i 1272 video...	Salvati 0 file - Erano già presenti 20352 file - File totali 20352
1272 video per il periodo (effettivo) da 2014-11-05 23:45:00 a 2014-11-10 10:00:00

3)  ->
Con cicloni: 105
Senza cicloni: 1047

Creazione delle folder per i 1152 video...	Salvati 0 file - Erano già presenti 18432 file - File totali 18432
1152 video per il periodo (effettivo) da 2014-11-29 19:45:00 a 2014-12-03 20:00:00

4)  ->
Con cicloni: 96
Senza cicloni: 972

Creazione delle folder per i 1068 video...	Salvati 0 file - Erano già presenti 17088 file - File totali 17088
1068 video per il periodo (effettivo) da 2016-02-27 16:45:00 a 2016-03-02 10:00:00

5)  ->
Con 

In [3]:
# Costruisce DataLoader per tracking a partire dal CSV generato
dm = DataManager(is_train=False, args=args, type_t='supervised', specify_data_path=csv_out)
track_loader = dm.get_tracking_dataloader(args)
track_ds = dm.dataset


Getting TRACKING dataset (pixel coords)...
DATASET length: 1118
Creo il DistributedSampler con world_size 1 e rank 0
Sampler_train = <torch.utils.data.distributed.DistributedSampler object at 0x7ff356e5af10>
Batch_size local: 1


In [ ]:
def extract_offsets(folder_path: str):
    """Parse tile top-left corner (x, y) from folder name."""
    base = os.path.basename(folder_path.rstrip(os.sep))
    nums = [int(n) for n in re.findall(r'\d+', base)]
    if len(nums) >= 2:
        return nums[-2], nums[-1]
    return 0, 0


In [9]:
# Grab a single example
video, coords, folder = track_ds[126]

# Undo normalization to [0, 1]
mean = torch.tensor([0.485, 0.456, 0.406]).view(3,1,1,1)
std = torch.tensor([0.229, 0.224, 0.225]).view(3,1,1,1)
video = (video * std + mean).clamp(0, 1)

# Convert to numpy [T, H, W, C]
video_np = video.permute(1, 2, 3, 0).numpy()

# coords are already tile-relative pixel coordinates (x, y)
px_tile, py_tile = coords.tolist()

# Draw the cyclone centre on each frame
frames = []
for frame in video_np:
    img = (frame * 255).astype(np.uint8)
    pil = Image.fromarray(img)
    draw = ImageDraw.Draw(pil)
    r = 4
    draw.ellipse((px_tile - r, py_tile - r, px_tile + r, py_tile + r), fill=(255, 0, 0))
    frames.append(np.asarray(pil) / 255.0)

# Display the clip
display_video_clip(frames)
